In [199]:
import numpy as np

class Maze(object):
    def __init__(self, num, numP, stateShape, dist=None, verbose=True):
        self.verbose=verbose
        self.numOfRooms=num
        self.numOfParticles=numP
        self.States=[i for i in range(num)]
        self.stateShape=stateShape
        if dist==None:  # initial distribution
            self.StatesDist=[int(self.numOfParticles/self.numOfRooms)]*self.numOfRooms
        else:  # uniform distribution
            self.StatesDist=dist
        if self.verbose:
            self.formattedPrint(self.StatesDist)
    def sampling(self, dist):
        total=sum(dist)
        dist= [dist[x]/total for x in self.States]
        return np.random.multinomial(self.numOfParticles,dist)
    def update(self, action, observ, setting):
        dist=setting.calcTransitionProb(action,self.StatesDist)
        if self.verbose: 
            print("After moving ", action, "=",end="\t") 
            self.formattedPrint(dist)
        dist=self.sampling(dist)
        if self.verbose: 
            print("Sampling ",  "\t=",end="\t") 
            self.formattedPrint(dist)
        weight = setting.calcWeight(dist,observ)
        if self.verbose: 
            print ("Observing ",observ, " (weight)=", end="\t")
            self.formattedPrint(weight)
        self.StatesDist = self.sampling(weight)
        if self.verbose: 
            print ("After resmpling =",end="\t")
            self.formattedPrint(self.StatesDist) 
            print("\n-----\n")
    def formattedPrint(self, dist):
        if self.numOfRooms < 8:
            self.printLine(dist)
            print()
        else:
            self.showRooms(dist)
    def printLine(self, dist):
        for x in dist:
            print("%0.2f"%(x),end="\t")
    def showRooms(self,dist):
        # num=self.numOfRooms # num should be 10
        # print(dist)
        print("\n[",end="\t")
        self.printLine(dist[:4])
        print("\n",end="\t")
        self.printLine(dist[4:7])
        print("\n",end="\t")
        self.printLine(dist[7:])
        print("]\n")

In [181]:
# room shape & ob : 1 [upper],2 [right], 4[lower], 8 [left]
class Setting(object):
    def __init__(self, transitionProb, observationProb, maze):
        self.tranProb=transitionProb
        self.obsProb=observationProb
        self.shapes=maze.stateShape
        self.States=maze.States
        self.numOfParticles=maze.numOfParticles
        self.actions=[self.possibleAction(s) for s in maze.stateShape]
    def possibleAction(self, room):
        actions=[]
        if (room % 2  == 0):
            actions +=['U']
        if ((room // 2) % 2 == 0):
            actions += ['R']
        if ((room //4) % 2 == 0):
            actions += ['D']
        if ((room // 8) % 2 == 0):
            actions += ['L']
        return actions
    def moveProb(self, newPos, oldPos, act):
        if (act == 'S'):  # stay
            if (newPos != oldPos):
                return 0.0
            else:
                return 1.0
        if (act not in self.actions[oldPos]):  # impossible move
            if (newPos == oldPos): # staying
                return 1.0
            else:
                return 0.0
        else:  # possible move
            if (newPos == oldPos):  #staying
                return 1-self.tranProb
            elif (act == 'R') and (newPos - oldPos == 1):
                return self.tranProb
            elif (act == 'L') and (oldPos - newPos == 1):
                return self.tranProb
            else:
                return 0.0
    def distProb(self, state, act, dist):
        return sum([self.moveProb(state, s, act)*dist[s] for s in self.States])
    def calcTransitionProb(self, act,dist):
        newdist = [self.distProb(state,act,dist) for state in self.States]
        return newdist
    def observationProb(self, observation, state):
        shape=self.shapes[state]
        if (observation == shape):
            return self.obsProb
        else:
            return (1.0 - self.obsProb)/15
    def calcWeight(self, dist, observ):
        weight=[self.observationProb(observ,s) for s in self.States]
        return list(map(lambda x,y: x*y,  dist, weight))
    def sampling(self, dist):
        total=sum(dist)
        dist= [dist[x]/total for x in self.States]
        return np.random.multinomial(self.numOfParticles,dist)


In [191]:
###### Reidai ########
reidai=Maze(5,10,[13, 5, 5, 5, 7])     # ob : 5 --- passage,  13 : left corner, 7 right corner
reidaiEnv=Setting(0.80, 0.70,reidai)

2.00	2.00	2.00	2.00	2.00	


In [192]:
reidaiEnv.actions

[['R'], ['R', 'L'], ['R', 'L'], ['R', 'L'], ['L']]

In [193]:
reidai.update('R',5,reidaiEnv)

After moving  R =	0.40	2.00	2.00	2.00	3.60	
Sampling  	=	1.00	2.00	0.00	3.00	4.00	
Observing  5  (weight)=	0.02	1.40	0.00	2.10	0.08	
After resmpling =	0.00	4.00	0.00	6.00	0.00	

-----



In [194]:
reidai.update('R',7,reidaiEnv)

After moving  R =	0.00	0.80	3.20	1.20	4.80	
Sampling  	=	0.00	1.00	3.00	1.00	5.00	
Observing  7  (weight)=	0.00	0.02	0.06	0.02	3.50	
After resmpling =	0.00	0.00	0.00	0.00	10.00	

-----



In [200]:
#################################################
# Exercise 9-2 - 9-4

print("\n\n  Exercise 9")
ex9_2=Maze(10,20,[9,1,1,7, 8,0,2, 12,4,6 ])     # ob : 1 [upper],2 [right], 4[lower], 8 [left]
ex9_2Env=Setting(0.80, 0.70, ex9_2)




  Exercise 9

[	2.00	2.00	2.00	2.00	
	2.00	2.00	2.00	
	2.00	2.00	2.00	]



In [201]:
print ("Action=staying:")
ex9_2.update('S',2,ex9_2Env)  # wall in the right hand

Action=staying:
After moving  S =	
[	2.00	2.00	2.00	2.00	
	2.00	2.00	2.00	
	2.00	2.00	2.00	]

Sampling  	=	
[	2.00	3.00	2.00	4.00	
	4.00	1.00	2.00	
	0.00	0.00	2.00	]

Observing  2  (weight)=	
[	0.04	0.06	0.04	0.08	
	0.08	0.02	1.40	
	0.00	0.00	0.04	]

After resmpling =	
[	1.00	1.00	0.00	0.00	
	0.00	0.00	18.00	
	0.00	0.00	0.00	]


-----



In [202]:
print ("Action=Moving Left:")
ex9_2.update('L',0,ex9_2Env)  # no walls 

Action=Moving Left:
After moving  L =	
[	1.80	0.20	0.00	0.00	
	0.00	14.40	3.60	
	0.00	0.00	0.00	]

Sampling  	=	
[	1.00	0.00	0.00	0.00	
	0.00	14.00	5.00	
	0.00	0.00	0.00	]

Observing  0  (weight)=	
[	0.02	0.00	0.00	0.00	
	0.00	9.80	0.10	
	0.00	0.00	0.00	]

After resmpling =	
[	0.00	0.00	0.00	0.00	
	0.00	20.00	0.00	
	0.00	0.00	0.00	]


-----

